In [1]:
import folium
import geopandas as gpd
import pandas as pd
import warnings
warnings.simplefilter("ignore")

In [2]:
up = gpd.read_file(r"F:\DSLR\Folium\Geojson\Upazilla_updated.geojson")
# dist = gpd.read_file(r"F:\DSLR\Folium\Geojson\BGD_adm2.geojson")

In [3]:
up_desc = pd.read_csv(r"F:\DSLR\Folium\Animate\describe.csv")
# dist_desc = pd.read_csv(r"F:\DSLR\Folium\Animate\District_desc.csv")

In [4]:
def get_div_cen(div_name):
    div_cen = {'Barisal': [22.419147168685168, 90.34719389574566],
                'Chittagong': [22.709657647813373, 91.73176862241395],
                'Dhaka': [23.839712023586152, 90.2416568363619],
                'Khulna': [22.917754757675876, 89.29251999630705],
                'Mymensingh': [24.846766716747663, 90.38045980128486],
                'Rajshahi': [24.588748960942787, 89.04457003840928],
                'Rangpur': [25.779405192595792, 89.05583622451685],
                'Sylhet': [24.71545553158574, 91.66406548888463]}
    return div_cen[div_name]

def df_process(up_desc, up_geo, div, dist, upz):
    if ("All" not in div):
        if ("All" in dist):
            sort_df = up_desc[up_desc.Division.isin(div)].reset_index(drop = True)
            sort_geo = up_geo[up_geo.ADM1_EN.isin(div)].reset_index(drop = True)
            if len(div) == 1:
                centroid = get_div_cen(div[0])
            else:
                center = up_geo[up_geo.ADM1_EN.isin(div)].unary_union.centroid
            zoom = 8
        else:
            if ("All" in upz):
                sort_df = up_desc[up_desc.District.isin(dist)].reset_index(drop = True)
                sort_geo = up_geo[up_geo.ADM2_EN.isin(dist)].reset_index(drop = True)
                center = up_geo[up_geo.ADM2_EN.isin(dist)].unary_union.centroid
                centroid = [center.y, center.x]
                zoom = 9
            else:
                sort_df = up_desc[up_desc.District.isin(dist)].reset_index(drop = True)
                sort_df = sort_df[sort_df.Upazilla.isin(upz)].reset_index(drop = True)
                sort_geo = up_geo[up_geo.ADM2_EN.isin(dist)].reset_index(drop = True)
                sort_geo = sort_geo[up_geo.ADM3_EN.isin(upz)].reset_index(drop = True)
                center = up_geo[up_geo.ADM2_EN.isin(dist)].unary_union.centroid
                centroid = [center.y, center.x]
                zoom = 9
    else:
        sort_df = up_desc
        sort_geo = up_geo
        centroid = [23.8103, 90.4125]
        zoom = 7

    return sort_df, sort_geo, centroid, zoom

    return sort_df, sort_geo, centroid, zoom

def get_tt(upz, dst, area, fh, crp, tca, crp_area, prcnt):
    
    if crp != "Cultivated_area":
        tooltip_html = """
        <div style="font-size: 14px">
        <b>Upazilla: </b> {upz}
        <br>
        <b>District: </b> {dst}
        <br>
        <b>Area: </b> {area} acre
        <br>
        <b>Firm Holdings: </b> {fh}
        <br>
        <b>Crop Area: </b> {tca} acre
        <br>
        <b>{crp} </b> {crp_area} acre ({prcnt}%)
        </div>
        """.format(upz=upz, dst=dst, area=area, fh=fh, crp=crp, tca=tca, crp_area=crp_area, prcnt=prcnt)
    else:
        tooltip_html = """
        <div style="font-size: 14px">
        <b>Upazilla: </b> {upz}
        <br>
        <b>District: </b> {dst}
        <br>
        <b>Area: </b> {area} acre
        <br>
        <b>Firm Holdings: </b> {fh}
        <br>
        <b>Crop Area: </b> {tca}
        <br>
        <b>{crp}: </b> {crp_area} acre
        </div>
        """.format(upz=upz, dst=dst, area=area, fh=fh, crp=crp, tca=tca, crp_area=crp_area, prcnt=prcnt)

    return tooltip_html

def circle_plot(centr, param, l_max, l_min, clr, clr_2, opacity_input, tooltip):
    
    shapesLayer = folium.FeatureGroup(name="Revenue")

    rad = get_rad(param, l_max, l_min)
    folium.Circle(location=[centr.y, centr.x],
                  radius= rad,
                  color=clr,
                  weight=2,
                  fill_color=clr_2,
                  fill_opacity= opacity_input,
                  tooltip = tooltip,
                  stroke = True).add_to(shapesLayer)
    return shapesLayer

def get_rad(loan = 0, l_max = 0, l_min = 0):
    
    px_min = 1000
    px_max = 10000
    
    final_rad = int(px_min + ((loan -l_min)*(px_max - px_min)/(l_max-l_min)))
    return final_rad

def get_op(f_num = 0, f_max = 0, f_min = 0):
    
    op_min = 0.3
    op_max = 0.7
    
    final_op = op_min + ((f_num -f_min)*(op_max - op_min)/(f_max-f_min))
    return final_op

def style_function(fill_color,fill_opacity):
    return lambda feature: {
        'color': "green",
        'weight': 2,
        'fillColor': fill_color,
        'fillOpacity': fill_opacity
    }

def get_fill(data, name, tooltip, clr, opacity):
    fill_obj = folium.GeoJson(
                    data=data,
                    name=name,
                    tooltip = tooltip,
                    style_function= style_function(clr, opacity),
                    highlight_function= lambda feat: {'fillColor': clr, 'fillOpacity': 1, 'weight': 2, 'color': 'green'}
                )
    
    return fill_obj

In [5]:
def init(up_desc, up_geo, div, dist, crop, weights):
    upz = 'All'
    sort_df, sort_geo, centroid, zoom = df_process(up_desc, up_geo, div, dist, upz)
    
    dataframe = up_desc
    df_type = 'Upazilla'
    geo_type = 'ADM3_EN'
    
    if len(crop) == 1:
        tt_crp = crop[0]
        op_min = (sort_df[tt_crp]/sort_df.Temporary_crops_net_area).min()
        op_max = (sort_df[tt_crp]/sort_df.Temporary_crops_net_area).max()
        rad_max = dataframe[tt_crp].max()
        rad_min = dataframe[tt_crp].min()
    else:
        tt_crp = 'Crops:'
        for i in range(len(crop)):
            if i == 0:
                per_sum = sort_df[crop[i]]/sort_df.Temporary_crops_net_area
            else:
                per_sum = per_sum + sort_df[crop[i]]/sort_df.Temporary_crops_net_area  
            tt_crp = tt_crp + ' ' + crop[i] + '(' + str(weights[i]* 100) + '%' + ')'
            if (len(crop) - i) > 1:
                tt_crp = tt_crp + ','
        sum_list = []
        for i in range(len(dataframe)):
            temp_sum = 0
            for j in range(len(crop)):
                temp_sum = temp_sum + dataframe[crop[j]][i]*weights[j]
            sum_list.append(temp_sum)
        rad_max = max(sum_list)
        rad_min = min(sum_list)
        op_max = per_sum.max()
        op_min = per_sum.min()
        
#         print(op_max, op_min)
        
    mapObj_dist = folium.Map(location=centroid, zoom_start=zoom, attr='Google', tiles='https://mt1.google.com/vt/lyrs=m&x={x}&y={y}&z={z}')
    
    for i in range(len(sort_df)):
        
        temp_df = sort_geo[sort_geo[geo_type] == sort_df[df_type][i]].reset_index(drop=True).iloc[[0]]
        
        if len(crop) == 1:
            op_2 = get_op(sort_df[tt_crp][i]/sort_df.Temporary_crops_net_area[i], op_max, op_min)
            tooltip = folium.Tooltip(get_tt(sort_df[df_type][i], sort_df.District[i], f"{int(int(sort_df.area[i])):,}",
                                           f"{int(sort_df.Total_firm_holdings_no[i]):,}",
                                           tt_crp, f"{int(sort_df.Temporary_crops_net_area[i]):,}",
                                            f"{int(sort_df[tt_crp][i]):,}",
                                           int(round((sort_df[tt_crp][i]/sort_df.Temporary_crops_net_area[i]*100),0))))
        else:
            for j in range(len(crop)):
                if j == 0:
                    tem_per = sort_df[crop[j]][i]/sort_df.Temporary_crops_net_area[i]
                else:
                    tem_per = tem_per + sort_df[crop[j]][i]/sort_df.Temporary_crops_net_area[i]
            wei_crop = 0
            for j in range(len(crop)):
                wei_crop = wei_crop + sort_df[crop[j]][i]*weights[j]
            op_2 = get_op(tem_per, op_max, op_min)
#             print(tem_per)
            tooltip = folium.Tooltip(get_tt(sort_df[df_type][i], sort_df.District[i], f"{int(int(sort_df.area[i])):,}",
                                           f"{int(sort_df.Total_firm_holdings_no[i]):,}",
                                           tt_crp, f"{int(sort_df.Temporary_crops_net_area[i]):,}",
                                            f"{int(wei_crop):,}",
                                           int(round((wei_crop/sort_df.Temporary_crops_net_area[i]*100),0))))
        
        fill_obj = get_fill(temp_df, temp_df[geo_type][0], tooltip, 'red', op_2)
        fill_obj.add_to(mapObj_dist)

    for i in range(len(sort_df)):
        
        temp_df = sort_geo[sort_geo[geo_type] == sort_df[df_type][i]].reset_index(drop=True).iloc[[0]]
        
        if len(crop)==1:
            tooltip = folium.Tooltip(get_tt(sort_df[df_type][i], sort_df.District[i], f"{int(int(sort_df.area[i])):,}",
                                           f"{int(sort_df.Total_firm_holdings_no[i]):,}",
                                           tt_crp, f"{int(sort_df.Temporary_crops_net_area[i]):,}",
                                            f"{int(sort_df[tt_crp][i]):,}",
                                           int(round((sort_df[tt_crp][i]/sort_df.Temporary_crops_net_area[i]*100),0))))
        else:
            wei_crop = 0
            for j in range(len(crop)):
                wei_crop = wei_crop + sort_df[crop[j]][i]*weights[j]
            tooltip = folium.Tooltip(get_tt(sort_df[df_type][i], sort_df.District[i], f"{int(int(sort_df.area[i])):,}",
                                           f"{int(sort_df.Total_firm_holdings_no[i]):,}",
                                           tt_crp, f"{int(sort_df.Temporary_crops_net_area[i]):,}",
                                            f"{int(wei_crop):,}",
                                           int(round((wei_crop/sort_df.Temporary_crops_net_area[i]*100),0))))

        centr = temp_df.geometry[0].centroid
        if len(crop)==1:
            shapesLayer = circle_plot(centr, sort_df[tt_crp][i]**1.025, rad_max, rad_min, 'blue', 'blue', 0.001, tooltip)
        else:
            shapesLayer = circle_plot(centr, wei_crop, rad_max, rad_min, 'blue', 'blue', 0.001, tooltip)
        shapesLayer.add_to(mapObj_dist)
        
    mapObj_dist.add_child(folium.LatLngPopup())
    
    return mapObj_dist

In [7]:
m = init(up_desc, up, ["Rajshahi"], ["Pabna", "Natore", "Rajshahi"], 
     ['Onion'], [0.1, 0.1, .1, 0.7])

m.save('Pab_nat_Raj_Onion.html')
m

In [ ]:
df_process(up_desc, up_geo, div, dist, upz)

In [27]:
descrb

NameError: name 'descrb' is not defined